# Notebook 3: Decision AI and Terrain

In this notebook, we explore developments to `battlesim` from version 0.3.4 including the new `Terrain` object and how terrains now impact the simulation.

### Requirements:

- `numpy`
- `pandas`
- `matplotlib`
- `numba`

In [1]:
import sys
sys.path.insert(0,"../")
# import
import battlesim as bsm

As before, we create a `Battle` object which is the main and only object you need to know about in the package, unless you wish to tweak some things under the hood.

In [2]:
bat = bsm.Battle("../datasets/starwars-clonewars.csv")
bat

bsm.Battle(init=False)

You may notice that a `T_` attribute for terrain is now present, and created, but not initialized:

In [3]:
bat.T_

Terrain(init=False, dtype='perlin', dims=(0.0, 10.0, 0.0, 10.0), resolution=0.100)

In addition, we have implemented **bounds** in the arena for the first time. This prevents units from leaving a certain bounds, which the `hit_and_run` decision AI had the tendency to simply keep running back and back, making it **too powerful** compared to basic aggressive tactics.

By default we set this to $(0, 10, 0, 10)$, corresponding to left, right, up and down respectively.

Bounds are checked at each time step in the simulation, by simply moving unit positions of units outside the box back into it:

\begin{equation}
B(x, y)=\begin{cases}
X_{min} & x < X_{min} \\
X_{max} & x > X_{max} \\
Y_{min} & y < Y_{min} \\
Y_{max} & y > Y_{max} 
\end{cases}
\end{equation}

Assuming movement speeds are relatively low, this keeps every unit in the plane.

In [4]:
bat.bounds_

(0.0, 10.0, 0.0, 10.0)

To modify these methods, make use of the `obj.set_bounds` and `obj.apply_terrain` methods. Note that setting the bounds or terrain before an *army* is initialized may cause clashes with the position-assignment of the units. What this means is that the unit spawner MUST spawn all units within the bounds before simulation starts. In practice, this just gives you a warning:

In [5]:
bat.set_bounds((-10, 20, -10, 20))

C:\Users\Gregory\Documents\Git\BattleSimulator\examples\..\battlesim\_battle.py:187: UserWarning: bounds (-10, 20, -10, 20) set before units are initialised - some may be out-of-bounds
  warnings.warn("bounds {} set before units are initialised - some may be out-of-bounds".format(b),


bsm.Battle(init=False)

When applying a terrain, we have a few options as to how we want it to look:

1. Use `None`, this tells the battle object that we want no terrain - i.e flat
2. Use `grid`, this makes a map of little color squares that have height
3. Use `contour`, this makes a map of filled contour lines that have height. In my opinion this one looks the best.

However, a terrain cannot be generated *until army groups have been defined*. Otherwise how can the bounds be properly determined?

In [6]:
armies1 = [
    bsm.Composite("Clone Trooper", 20, bsm.Sampling("normal", -2., 2.)),
    bsm.Composite("B1 battledroid", 50, bsm.Sampling("normal", 5., 2.)),
]

bat.create_army(armies1)

bsm.Battle(init=False)

In [7]:
bat.composition_

[Composite('Clone Trooper', n=20, pos=Sampling('normal', (-2.0, 2.0)), init_ai='nearest', rolling_ai='nearest', decision_ai='aggressive'),
 Composite('B1 battledroid', n=50, pos=Sampling('normal', (5.0, 2.0)), init_ai='nearest', rolling_ai='nearest', decision_ai='aggressive')]

Did this change the boundary?

In [8]:
bat.bounds_

(-10, 20, -10, 20)

So calls to `create_army` will try and re-assign new boundaries respective of the units. However they might be a bit *hemmed in*.

Note that, by using the `None` as input, I am essentially defining a flat terrain:

In [9]:
bat.apply_terrain(None)

bsm.Battle(init=False)

A call to `apply_terrain` does however generate a map, which can be accessed through the height `Z_` attribute in the terrain, which only appears once the simulation has been called:

In [10]:
bat.T_.Z_

I think we're ready to simulate...

In [11]:
F = bat.simulate()

In [12]:
bat.sim_jupyter()

## With Terrain Modification

Terrains currently serve to **reduce the movement speed** of units by up to 50% when moving on a hill. To specify a terrain, use `apply_terrain` and use either `grid` or `contour`.

Mathematically, movement calculations are *currently* determined at timestep $t$ with $u \in [x, y]$ as:

\begin{align}
\dot{u}_{i,t} \approx s_i \left(1-\frac{z_{i}}{2}\right) \frac{\delta u_{i,t}}{||\delta u_{i,t} ||}
\end{align}

where $s_i$ is the unit base speed, $\delta u_i$ is the directional derivative with respect to it's enemy, $||\delta u_i ||$ is the distance of unit $i$ from the enemy $j$, and $z_{i}$ is the height measured at the node nearest to $u_i$. indices of $z$ are determined as:

\begin{align}
z_{ind}=\arg \min \left|u_{i,t}-\Omega \right|
\end{align}

where $\Omega$ is the meshgrid domain. Note that $z$ can be from a function defined by the user as $z=f(\Omega)$, or generated from Perlin noise (default).

In [13]:
bat.apply_terrain("contour")

bsm.Battle(init=True, n_armies=2, simulated=True)

In [14]:
bat.bounds_

(-7.0, 9.0, -6.0, 9.0)

Now if we re-run:

In [15]:
F = bat.simulate()
bat.sim_jupyter()

A *marked difference* in performance, the units on the hill move substantially slower, giving the other team a chance to pick off the enemy units in a more stream-like fashion.

Notice that with each re-run the hill(s) should spawn in different locations.

## Using Hit-and-Run

Let's see how the Republic fares when we incorporate the `hit_and_run` AI:

In [16]:
bat._comps[0].decision_ai = "hit_and_run"

In [17]:
F = bat.simulate()
bat.sim_jupyter()

You will notice that the Republic performs **substantially better** using this more complex AI path than simple *aggressive* strategies.

Let's perform a test to see if this AI strategy alone can improve outcomes using `simulate_k`.

This can be found very elegantly since most of the functions in `Battle` return self which means we can *function chain*:

This is the end to the third notebook.